### Political Conflicts in Germany in 2021

Localized maps based on <a href="https://towardsdatascience.com/level-up-your-visualizations-make-interactive-maps-with-python-and-bokeh-7a8c1da911fd" target="_blank">this work</a>.

In [2]:
#import packages

import pandas as pd
import numpy as np

from bokeh.models import *
from bokeh.plotting import *
from bokeh.io import *
from bokeh.tile_providers import *
from bokeh.palettes import *
from bokeh.transform import *
from bokeh.layouts import *

In [3]:
#import and clean the data

conflict_df = pd.read_csv('data_germany.csv', skiprows=None)
conflict_df = conflict_df[conflict_df['year'] == 2021]
#conflict_df = conflict_df[conflict_df['event_type'] != "Protests"]

In [4]:
conflict_df['latitude'] = conflict_df['latitude'].astype('float')
conflict_df['longitude'] = conflict_df['longitude'].astype('float')
conflict_df['fatalities'] = conflict_df['fatalities'].astype('int64')
conflict_df = conflict_df.reset_index()
conflict_df = conflict_df.drop('index',axis=1)

In [5]:
#sanity check
conflict_df

data_id  iso event_id_cnty  event_id_no_cnty       event_date  year  \
0     8602316  276       DEU8358              8358  15 October 2021  2021   
1     8602522  276       DEU8359              8359  15 October 2021  2021   
2     8602599  276       DEU8335              8335  15 October 2021  2021   
3     8602862  276       DEU8345              8345  15 October 2021  2021   
4     8602625  276       DEU8351              8351  14 October 2021  2021   
...       ...  ...           ...               ...              ...   ...   
3559  7464285  276       DEU4783              4783  02 January 2021  2021   
3560  7490185  276       DEU4785              4785  02 January 2021  2021   
3561  7491678  276       DEU4784              4784  02 January 2021  2021   
3562  7496643  276       DEU4819              4819  01 January 2021  2021   
3563  7762301  276       DEU4809              4809  01 January 2021  2021   

      time_precision              event_type                sub_event_type  \
0                  1                   Riots         Violent demonstration   
1                  1                   Riots         Violent demonstration   
2                  1                Protests              Peaceful protest   
3                  1                Protests              Peaceful protest   
4                  2                Protests              Peaceful protest   
...              ...                     ...                           ...   
3559               1                Protests              Peaceful protest   
3560               1                Protests              Peaceful protest   
3561               1                Protests              Peaceful protest   
3562               1                 Battles              Peaceful protest   
3563               1  Strategic developments  Looting/property destruction   

                                  actor1  ...       location  latitude  \
0                      Rioters (Germany)  ...        Hamburg   53.5507   
1                      Rioters (Germany)  ...         Berlin   52.5244   
2                   Protesters (Germany)  ...          Fulda   50.5523   
3                   Protesters (Germany)  ...      Wiesbaden   50.0822   
4                   Protesters (Germany)  ...     Volkmarsen   51.4129   
...                                  ...  ...            ...       ...   
3559                Protesters (Germany)  ...         Berlin   52.5244   
3560                Protesters (Germany)  ...      Straubing   48.8828   
3561                Protesters (Germany)  ...       Nurnberg   49.4552   
3562                Protesters (Germany)  ...  Rommelshausen   48.8074   
3563  Unidentified Armed Group (Germany)  ...      Magdeburg   52.1307   

     longitude geo_precision                                      source  \
0       9.9930             1  Hamburger Abendblatt; Weser Kurier Politik   
1      13.4105             1                            Der Tagesspiegel   
2       9.6762             1                             Fuldaer Zeitung   
3       8.2418             1                                         RGA   
4       9.1156             1       Hessische Niedersachsische Allgemeine   
...        ...           ...                                         ...   
3559   13.4105             1    Suddeutsche Zeitung; Berliner Morgenpost   
3560   12.5690             1                        Passauer Neue Presse   
3561   11.0783             1                                        RIAS   
3562    9.3210             1                                         ZVW   
3563   11.6420             1                         Indymedia (Germany)   

              source_scale                                              notes  \
0     Subnational-National  On 15 October 2021, around 500 of people, incl...   
1              Subnational  On 15 October 2021, more than 5000 people, inc...   
2                 National  On 15 October 2021, around 250 people, mostly ...   
3                 

In [18]:
#Bokeh maps are in mercator. Convert lat lon fields to mercator units for plotting

def wgs84_to_web_mercator(df, lon, lat):
    """Converts decimal longitude/latitude to Web Mercator format"""
    k = 6378137
    df["x"] = df[lon] * (k * np.pi/180.0)
    df["y"] = np.log(np.tan((90 + df[lat]) * np.pi/360.0)) * k
    return df

df=wgs84_to_web_mercator(conflict_df,'longitude','latitude')

#Establishing a zoom scale for the map. The scale variable will also determine proportions for hexbins and bubble maps so that everything looks visually appealing. 

scale = 2000
x = df['x']
y = df['y']

#The range for the map extents is derived from the lat/lon fields. This way the map is automatically centered on the plot elements.

x_min = int(x.mean() - (scale * 350))
x_max = int(x.mean() + (scale * 350))
y_min = int(y.mean() - (scale * 350))
y_max = int(y.mean() + (scale * 350))

#Defining the map tiles to use. I use OSM, but you can also use ESRI images or google street maps.

tile_provider = get_provider(OSM)

#Establish the bokeh plot object and add the map tile as an underlay. Hide x and y axis.

plot = figure(
    title='2021 Political Conflicts in Germany',
    match_aspect=True,
    tools='wheel_zoom,pan,reset,save',
    x_range=(x_min, x_max),
    y_range=(y_min, y_max),
    x_axis_type='mercator',
    y_axis_type='mercator',
    width=1000
    )

plot.grid.visible=True

map = plot.add_tile(tile_provider)
map.level='underlay'

plot.xaxis.visible = False
plot.yaxis.visible=False
plot.title.text_font_size="20px"

output_notebook()

Loading BokehJS ...

In [19]:
#function takes scale (defined above), the initialized plot object, and the converted dataframe with mercator coordinates to create a hexbin map

def hex_map(plot,df, scale,leg_label='Hexbin Heatmap'):
    r,bins = plot.hexbin(x,y,size=scale*10,hover_color='pink',hover_alpha=0.8,legend_label=leg_label)
    hex_hover = HoverTool(tooltips=[('count','@c')],mode='mouse',point_policy='follow_mouse',renderers=[r])
    hex_hover.renderers.append(r)
    plot.tools.append(hex_hover)

    plot.legend.location = "top_right"
    plot.legend.click_policy="hide"

#function takes a column to determine radius and the dataframe with converted mercator coordinates to create a bubble map. 
def bubble_map(plot,df,radius_col,lon,lat,scale,color='orange',leg_label='Bubble Map'):
    radius = []
    for i in df[radius_col]:
        radius.append(i*scale)

    df['radius']=radius

    source=ColumnDataSource(df)
    c=plot.circle(x='x',y='y',color=color,source=source,size=1,fill_alpha=0.4,radius='radius',legend_label=leg_label,hover_color='red')

    tip_label='@'+radius_col
    lat_label='@'+lat
    lon_label='@'+lon

    circle_hover = HoverTool(tooltips=[(radius_col,tip_label),('Lat:',lat_label),('Lon:',lon_label)],mode='mouse',point_policy='follow_mouse',renderers=[c])
    circle_hover.renderers.append(c)
    plot.tools.append(circle_hover)

#The legend.click_policy method allows us to toggle layer on/off by clicking the corresponding field in the legend. We'll explore this more later!
plot.legend.location = "top_right"
plot.legend.click_policy = "hide"

In [20]:
#Create the hexbin map
hex_map(plot=plot,
        df=conflict_df, 
        scale=scale,
        leg_label='German Conflict Events by Number of Events')

In [21]:
#Create the bubble map. In this case, circle radius is defined by the amount of fatalities. Any column can be chosen to define the radius.
bubble_map(plot=plot,
           df=conflict_df,
           radius_col='fatalities', 
           leg_label='German Conflict Events by Fatality',
           lon='longitude',
           lat='latitude',
           scale=scale)

In [22]:
#Creating a second map that will display events categorically by type

cat_map = figure(
    title='2021 German Conflict Events by Category',
    match_aspect=True,
    tools='wheel_zoom,pan,reset,save',
    x_range=(x_min, x_max),
    y_range=(y_min, y_max),
    x_axis_type='mercator',
    y_axis_type='mercator',
    width=1000)

cat_map.grid.visible = True

m = cat_map.add_tile(tile_provider)
m.level='underlay'

cat_map.xaxis.visible = False
cat_map.yaxis.visible = False
cat_map.title.text_font_size = "20px"

In [25]:
'''Removing duplicate event types using the dictionary method. 
Though there are other ways to remove duplicates from a list, this is my preferred method for simplicity.'''

events = list(conflict_df['event_type'].dropna(how=None))
event_dict = dict.fromkeys(events,0)
events = list(event_dict)

#Initializing empty lists to create temporary dataframes for each category
Protests=[]
Strategic_developments=[]
Riots=[]
Battles=[]
Explosions_remote_violence=[]
Violence_against_civilians=[]
list_list=[Riots,Protests,Strategic_developments,Violence_against_civilians,Explosions_remote_violence,Battles]


#Extracting event information for each category. I opted not to use nested iterators here to enhance code readability - a more efficient method woudld be to use a nested for loop with 'for iterate1,iterate2 in zip (event_type_name,list_name)
for i in range(len(df['event_type'])):
  if df.loc[i,'event_type']=='Protests':
    Protests.append([df.loc[i,'event_type'],
                     df.loc[i,'x'],df.loc[i,'y'],
                     df.loc[i,'actor1'],
                     df.loc[i,'notes'],
                     df.loc[i,'latitude'],
                     df.loc[i,'longitude']])

for i in range(len(df['event_type'])):
  if df.loc[i,'event_type']=='Strategic developments':
    Strategic_developments.append([df.loc[i,'event_type'],
                                   df.loc[i,'x'],
                                   df.loc[i,'y'],
                                   df.loc[i,'actor1'],
                                   df.loc[i,'notes'],
                                   df.loc[i,'latitude'],
                                   df.loc[i,'longitude']])

for i in range(len(df['event_type'])):
  if df.loc[i,'event_type']=='Riots':
    Riots.append([df.loc[i,'event_type'],
                  df.loc[i,'x'],
                  df.loc[i,'y'],
                  df.loc[i,'actor1'],
                  df.loc[i,'notes'],
                  df.loc[i,'latitude'],
                  df.loc[i,'longitude']])

for i in range(len(df['event_type'])):
  if df.loc[i,'event_type']=='Battles':
    Battles.append([df.loc[i,'event_type'],
                    df.loc[i,'x'],
                    df.loc[i,'y'],
                    df.loc[i,'actor1'],
                    df.loc[i,'notes'],
                    df.loc[i,'latitude'],
                    df.loc[i,'longitude']])

for i in range(len(df['event_type'])):
  if df.loc[i,'event_type']=='Explosions/Remote violence':
    Explosions_remote_violence.append([df.loc[i,'event_type'],
                                       df.loc[i,'x'],
                                       df.loc[i,'y'],
                                       df.loc[i,'actor1'],
                                       df.loc[i,'notes'],
                                       df.loc[i,'latitude'],
                                       df.loc[i,'longitude']])

for i in range(len(df['event_type'])):
  if df.loc[i,'event_type']=='Violence against civilians':
    Violence_against_civilians.append([df.loc[i,'event_type'],
                                       df.loc[i,'x'],df.loc[i,'y'],
                                       df.loc[i,'actor1'],
                                       df.loc[i,'notes'],
                                       df.loc[i,'latitude'],
                                       df.loc[i,'longitude']])

In [30]:
#using the list of lists, create temporary dataframes for each event category and plot them to our second map.

for i in range(len(list_list)):
    temp_df = pd.DataFrame(list_list[i],columns=['event_type','x','y','actor1','notes','latitude','longitude'])
    source = ColumnDataSource(temp_df)

    circle = cat_map.circle(x='x',y='y',source=source,color=Accent6[i],line_color=Accent6[i],legend_label=events[i],hover_color='white',radius=15000,fill_alpha=0.8)

    event_hover = HoverTool(tooltips=[('Actor','@actor1'),
                                    ('Category','@event_type'),
                                    ('Description','@notes'),
                                    ('(Lat,Lon)','(@latitude,@longitude)')],
                          mode='mouse',
                          point_policy='follow_mouse',
                          renderers=[circle])
  
    event_hover.renderers.append(circle)
    cat_map.tools.append(event_hover)

#View our maps

cat_map.legend.location = "top_right"
cat_map.legend.click_policy = "hide"

output_file('/Users/max/Dropbox/Python BI Udemy Kurs/Political_Conflicts_in_Germany/maps.html')
show(column(plot,cat_map))